In [1]:
import os

from dotenv import load_dotenv
from smolagents import CodeAgent, VisitWebpageTool

from asr import speech_to_text
from browser import TavilySearchTool
from downloader import download_file_to_temp
from models import AzureOpenAIServerModel
from pdf_reader import read_pdf_file
from scorer import question_scorer
from visual_qa import visual_qa

load_dotenv()

/home/mila/i/islamria/miniconda3/envs/ml/lib/python3.11/site-packages/pypdf/_crypt_providers/_cryptography.py:32: CryptographyDeprecationWarning: ARC4 has been moved to cryptography.hazmat.decrepit.ciphers.algorithms.ARC4 and will be removed from cryptography.hazmat.primitives.ciphers.algorithms in 48.0.0.
  from cryptography.hazmat.primitives.ciphers.algorithms import AES, ARC4
/home/mila/i/islamria/miniconda3/envs/ml/lib/python3.11/site-packages/pydantic/_internal/_config.py:345: UserWarning: Valid config keys have changed in V2:
* 'fields' has been removed
  warnings.warn(message, UserWarning)


True

In [2]:
model = AzureOpenAIServerModel(
    model_id=os.getenv("MODEL_NAME"),
    azure_endpoint=os.getenv("AZURE_BASE"),
    api_key=os.getenv("AZURE_API_KEY"),
    api_version=os.getenv("AZURE_API_VERSION"),
)

web_search = TavilySearchTool(os.getenv("TAVILY_API_KEY"))
visit_webpage = VisitWebpageTool()
tools = [
    web_search,
    visit_webpage,
    download_file_to_temp,
    read_pdf_file,
    visual_qa,
    speech_to_text,
]

agent = CodeAgent(
    tools=tools,
    model=model,
    add_base_tools=False,
    additional_authorized_imports=[
        "requests",
        "bs4",
        "wikipedia",
        "openpyxl",
        "pandas",
        "docx",
        "pptx",
        "sympy",
        "functools",
    ],
)

In [3]:
from datasets import load_dataset

ds = load_dataset("gaia-benchmark/GAIA", "2023_level1")
subset = ds["validation"]
file_dir = "data/gaia/validation"

In [4]:
import shutil

from tqdm.auto import tqdm

answers = []
total = 0
correct = 0
pbar = tqdm(subset)

for data in pbar:
    file_name = data["file_name"]
    task = data["Question"]

    if file_name:
        src = os.path.join(file_dir, file_name)
        shutil.copy(src, file_name)
        task += "\nAttachments in the current directory: " + file_name

    final_answer = agent.run(task)

    if file_name:
        os.remove(file_name)

    correct += question_scorer(str(final_answer), data["Final answer"])
    total += 1

    answers.append(final_answer)
    pbar.set_postfix({"Correct": f"{correct}/{total}"})

pbar.close()

  0%|          | 0/53 [00:00<?, ?it/s]

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ If Eliud Kipchoge could maintain his record-making marathon pace indefinitely, how many thousand hours would it │
│ take him to run the distance between the Earth and the Moon its closest approach? Please use the minimum        │
│ perigee value on the Wikipedia page for the Moon when carrying out your calculation. Round your result to the   │
│ nearest 1000 hours and do not use any comma separators if necessary.                                            │
│                                                                                                                 │
╰─ AzureOpenAIServerModel - gpt-4o-900ptu ────────────────────────────────────────────────────────────────────────╯

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 0 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

─ Executing this code: ────────────────────────────────────────────────────────────────────────────────────────── 
  # Eliud Kipchoge's marathon record time in seconds (Berlin Marathon 2018): 2 hours, 1 minute, 39 seconds         
  kipchoge_time_seconds = (2 * 3600) + (1 * 60) + 39  # Total time in seconds                                      
                                                                                                                   
  # Standard marathon distance in meters                                                                           
  marathon_distance_meters = 42195  # Distance in meters                                                           
                                                                                                                   
  # Calculate his pace (meters per second)                                                                         
  kipchoge_pace_mps = marathon_distance_meters / kipchoge_time_seconds                                             
  print(kipchoge_pace_mps)                                                                                         
 ─────────────────────────────────────────────────────────────────────────────────────────────────────────────────

Execution logs:
5.780928894369092

Out: None

...

[Step 5: Duration 3.38 seconds| Input tokens: 30,130 | Output tokens: 930]

Reached max steps.

Final answer: The first name of the only Malko Competition recipient from the 20th Century (after 1977) whose 
nationality on record is from a country that no longer exists is Gotthard. Gotthard Lienicke was likely from East 
Germany, a country that ceased to exist after reunification with West Germany in 1990.

[Step 6: Duration 0.00 seconds| Input tokens: 35,722 | Output tokens: 999]

Evaluating The first name of the only Malko Competition recipient from the 20th Century (after 1977) whose nationality on record is from a country that no longer exists is Gotthard. Gotthard Lienicke was likely from East Germany, a country that ceased to exist after reunification with West Germany in 1990. as a string.
